## CÉLULA 0 — Cabeçalho e Sumário Executivo

# CIP — Demonstração de Interoperabilidade Espectral entre SDKs (IDX 18 / IDX 20)

Este notebook demonstra, de forma reprodutível, que a CIP mantém **coerência espectral** e 
**interoperabilidade estrutural** entre SDKs distintos, associados a índices públicos (IDX) diferentes.

Trabalharemos com dois SDKs oficiais:

- **SDK Linux — IDX 18**
- **SDK Windows — IDX 20**

Ambos foram utilizados para assinar o **mesmo arquivo**, em modo TOTAL (`-t`).  
O objetivo aqui é mostrar que:

1. **Um único arquivo**, assinado por dois SDKs distintos (IDX 18 e IDX 20), gera chaves diferentes;
2. **O mesmo binário CIP** (nativo da máquina onde o notebook está rodando) é capaz de:
   - validar o arquivo com a chave do SDK Linux (IDX 18);
   - validar o arquivo com a chave do SDK Windows (IDX 20);
3. A decisão de integridade **não depende**:
   - do sistema operacional onde a assinatura foi gerada,
   - do SDK específico utilizado,
   - nem do compilador que produziu o binário;
4. Quando o arquivo é corrompido (alteração mínima, 1 bit), **ambas** as chaves deixam de validar;
5. A interoperabilidade é consequência direta da **régua espectral única** — não de ajustes *ad hoc* de implementação.

Este notebook não recompila SDKs, nem gera novas assinaturas.  
Ele parte de um cenário realista: SDKs já distribuídos e chaves já emitidas, e verifica a coerência do protocolo.


## CÉLULA 1 — Imports, detecção de SO e configuração básica

Aqui vamos seguir a mesma linha do notebook anterior: detectar SO, definir diretórios e preparar utilitários.

In [1]:
# ============================================================
# CÉLULA 1 — Configuração básica de ambiente
# ============================================================

import os
import stat
import shutil
import zipfile
import subprocess
import time
import random

from pathlib import Path

import pandas as pd
import matplotlib.pyplot as plt
from tqdm import tqdm

# Diretório base (local do notebook)
BASE_DIR = Path.cwd()
print(f"[INFO] Diretório base do notebook: {BASE_DIR}")

# Sistema operacional
WINDOWS = os.name == "nt"
print(f"[INFO] Sistema detectado: {'Windows' if WINDOWS else 'Linux'}")

# ------------------------------------------------------------
# Estrutura de diretórios do experimento
# ------------------------------------------------------------
SDK_DIR        = BASE_DIR / "sdk_local"          # onde o SDK nativo será extraído
CHAVES_DIR     = BASE_DIR / "chaves_interop"     # onde colocaremos as duas chaves (Linux/Windows)
ARQUIVOS_DIR   = BASE_DIR / "arquivos"           # onde ficará o arquivo de teste
RESULTADOS_DIR = BASE_DIR / "resultados"         # para tabelas e artefatos

for d in [SDK_DIR, CHAVES_DIR, ARQUIVOS_DIR, RESULTADOS_DIR]:
    d.mkdir(exist_ok=True)
    print(f"[OK] Diretório garantido: {d}")

# Limite de segurança para tamanho de arquivo (1 GB)
LIMITE_BYTES = 1_000_000_000
print(f"[INFO] Limite de tamanho de arquivo: {LIMITE_BYTES/1e6:.1f} MB")


[INFO] Diretório base do notebook: /home/alvaro/cip_viana
[INFO] Sistema detectado: Linux
[OK] Diretório garantido: /home/alvaro/cip_viana/sdk_local
[OK] Diretório garantido: /home/alvaro/cip_viana/chaves_interop
[OK] Diretório garantido: /home/alvaro/cip_viana/arquivos
[OK] Diretório garantido: /home/alvaro/cip_viana/resultados
[INFO] Limite de tamanho de arquivo: 1000.0 MB


## CÉLULA 2 — Download (ou uso local) do SDK nativo

Aqui vamos assumir que, para o notebook de interoperabilidade, você vai disponibilizar um SDK nativo único:

Se o usuário estiver em Linux → cip-sdk-linux-idx18.zip

Se estiver em Windows → cip-sdk-windows-idx20.zip

A interoperabilidade conceptual não depende de qual é o “nativo”; o foco é: um binário local verificando chaves de SDKs distintos.

In [2]:
# ============================================================
# CÉLULA 2 — Download e extração do SDK nativo
# ============================================================

# Aqui definimos o ZIP esperado de acordo com o sistema
if WINDOWS:
    ZIP_NAME = "cip-sdk-windows-idx20.zip"
    SDK_FOLDER_NAME = "cip-sdk-windows-idx20"
    DOWNLOAD_URL = "https://api.delta-cip.com.br/downloads/93ff0e11df434ba2bfcaa40b3dd3aad1/cip-sdk-windows-idx20.zip"
else:
    ZIP_NAME = "cip-sdk-linux-idx18.zip"
    SDK_FOLDER_NAME = "cip-sdk-linux-idx18"
    DOWNLOAD_URL = "https://api.delta-cip.com.br/downloads/d5784b5dca9b444fafcbb2aa9c9f5c01/cip-sdk-linux-idx18.zip"

ZIP_PATH = BASE_DIR / ZIP_NAME
SDK_FOLDER_PATH = SDK_DIR / SDK_FOLDER_NAME

print(f"[INFO] ZIP esperado: {ZIP_NAME}")
print(f"[INFO] Pasta local do SDK: {SDK_FOLDER_PATH}")

# ------------------------------------------------------------
# 1. Se a pasta do SDK já existir, usamos diretamente
# ------------------------------------------------------------
if SDK_FOLDER_PATH.exists():
    print(f"[OK] SDK já disponível em: {SDK_FOLDER_PATH}")
else:
    # --------------------------------------------------------
    # 2. Se o ZIP não existir localmente, baixamos
    # --------------------------------------------------------
    if not ZIP_PATH.exists():
        import requests

        print(f"[INFO] Baixando SDK a partir de:\n{DOWNLOAD_URL}\n")
        with requests.get(DOWNLOAD_URL, stream=True) as r:
            r.raise_for_status()
            with open(ZIP_PATH, "wb") as f:
                for chunk in r.iter_content(chunk_size=8192):
                    if chunk:
                        f.write(chunk)
        print(f"[OK] Download concluído: {ZIP_PATH}")
    else:
        print(f"[OK] ZIP encontrado localmente: {ZIP_PATH}")

    # --------------------------------------------------------
    # 3. Extração do SDK
    # --------------------------------------------------------
    print(f"[INFO] Extraindo SDK para: {SDK_FOLDER_PATH}")
    SDK_FOLDER_PATH.mkdir(parents=True, exist_ok=True)
    with zipfile.ZipFile(ZIP_PATH, "r") as z:
        z.extractall(SDK_FOLDER_PATH)

    print("[OK] SDK extraído com sucesso.")

# ------------------------------------------------------------
# 4. Localizar o binário nativo da CIP
# ------------------------------------------------------------
if WINDOWS:
    CIP_BIN = SDK_FOLDER_PATH / "bin" / "cip.exe"
else:
    CIP_BIN = SDK_FOLDER_PATH / "bin" / "cip"

if not CIP_BIN.exists():
    raise FileNotFoundError(f"[ERRO] Binário CIP não encontrado em: {CIP_BIN}")

# Garantir permissão de execução no Linux
if not WINDOWS:
    st = os.stat(CIP_BIN)
    os.chmod(CIP_BIN, st.st_mode | stat.S_IXUSR | stat.S_IXGRP | stat.S_IXOTH)

print(f"[OK] Binário CIP localizado em: {CIP_BIN}")


[INFO] ZIP esperado: cip-sdk-linux-idx18.zip
[INFO] Pasta local do SDK: /home/alvaro/cip_viana/sdk_local/cip-sdk-linux-idx18
[OK] SDK já disponível em: /home/alvaro/cip_viana/sdk_local/cip-sdk-linux-idx18
[OK] Binário CIP localizado em: /home/alvaro/cip_viana/sdk_local/cip-sdk-linux-idx18/bin/cip


## CÉLULA 3 — Função utilitária `run_cip` e explicação da lógica de interoperabilidade

Aqui copiamos a função `run_cip` (como no notebook 1) e já deixamos explicado que vamos usar um único binário para verificar duas chaves geradas por SDKs com IDX distintos.

In [3]:
# ============================================================
# CÉLULA 3 — Utilitário para executar o binário CIP
# ============================================================

def run_cip(args):
    """
    Executa o binário CIP com os argumentos dados,
    medindo tempo de execução e capturando stdout/stderr.
    """
    inicio = time.time()
    proc = subprocess.run(
        [str(CIP_BIN)] + args,
        cwd=SDK_FOLDER_PATH,
        capture_output=True,
        text=True,
        encoding="utf-8",
        errors="replace",
    )
    duracao = time.time() - inicio
    return proc, duracao

print("[OK] Função run_cip configurada.")

print(
    "\nNeste notebook, usaremos **um único binário CIP nativo** "
    "para verificar chaves geradas por SDKs distintos (IDX 18 e IDX 20)."
)
print(
    "A lógica de interoperabilidade é simples: se o arquivo permanece idêntico, "
    "qualquer SDK compatível com a régua espectral única deve validar a integridade."
)


[OK] Função run_cip configurada.

Neste notebook, usaremos **um único binário CIP nativo** para verificar chaves geradas por SDKs distintos (IDX 18 e IDX 20).
A lógica de interoperabilidade é simples: se o arquivo permanece idêntico, qualquer SDK compatível com a régua espectral única deve validar a integridade.


## CÉLULA 4 — Download do arquivo de teste + cópia local das duas chaves com `tqdm`

In [4]:
# ============================================================
# CÉLULA 4 — Download NOAA + Chaves (IDX 18 / IDX 20) com tqdm
# ============================================================

import requests
from tqdm import tqdm

# URLs públicas do site
BASE_URL = "https://delta-cip.com.br/downloads"

ARQ_REMOTE            = f"{BASE_URL}/noaa_gsod_2023.tar.gz"
CHAVE_LINUX_REMOTE   = f"{BASE_URL}/chave_cipt_assinado_idx18_N1024_20251124_115945.json"
CHAVE_WINDOWS_REMOTE = f"{BASE_URL}/chave_cipt_assinado_idx20_N1024_20251124_120307.json"

ARQ_LOCAL            = ARQUIVOS_DIR / "noaa_gsod_2023.tar.gz"
CHAVE_LINUX_LOCAL    = CHAVES_DIR   / "chave_idx18_linux.json"
CHAVE_WINDOWS_LOCAL  = CHAVES_DIR   / "chave_idx20_windows.json"

# ------------------------------------------------------------
# Função com tqdm
# ------------------------------------------------------------
def baixar_com_progresso(url: str, destino: Path):
    """
    Faz download com barra de progresso.
    Não baixa novamente se o arquivo já existir.
    """
    if destino.exists() and destino.stat().st_size > 0:
        print(f"[OK] Já existe localmente: {destino} ({destino.stat().st_size/1e6:.2f} MB)")
        return

    print(f"[INFO] Baixando: {url}")

    with requests.get(url, stream=True) as r:
        r.raise_for_status()

        total = int(r.headers.get("content-length", 0))
        blocos = 8192

        # barra de progresso
        barra = tqdm(total=total, unit="B", unit_scale=True, desc=destino.name)

        with open(destino, "wb") as f:
            for chunk in r.iter_content(chunk_size=blocos):
                if chunk:
                    f.write(chunk)
                    barra.update(len(chunk))

        barra.close()

    print(f"[OK] Download concluído: {destino} ({destino.stat().st_size/1e6:.2f} MB)")


# ------------------------------------------------------------
# Baixar arquivo NOAA + chaves
# ------------------------------------------------------------
baixar_com_progresso(ARQ_REMOTE, ARQ_LOCAL)
baixar_com_progresso(CHAVE_LINUX_REMOTE, CHAVE_LINUX_LOCAL)
baixar_com_progresso(CHAVE_WINDOWS_REMOTE, CHAVE_WINDOWS_LOCAL)

print("\n[OK] Arquivo e chaves importados para o notebook:")
print(f"  - Arquivo NOAA............: {ARQ_LOCAL}")
print(f"  - Chave Linux (IDX 18)....: {CHAVE_LINUX_LOCAL}")
print(f"  - Chave Windows (IDX 20)..: {CHAVE_WINDOWS_LOCAL}")

# Segurança básica: tamanho
tamanho_bytes = ARQ_LOCAL.stat().st_size
print(f"\nTamanho do arquivo NOAA: {tamanho_bytes/1e6:.2f} MB")

if tamanho_bytes == 0 or tamanho_bytes > LIMITE_BYTES:
    raise RuntimeError("Arquivo ausente, corrompido ou fora do limite permitido.")


[OK] Já existe localmente: /home/alvaro/cip_viana/arquivos/noaa_gsod_2023.tar.gz (108.78 MB)
[OK] Já existe localmente: /home/alvaro/cip_viana/chaves_interop/chave_idx18_linux.json (0.09 MB)
[OK] Já existe localmente: /home/alvaro/cip_viana/chaves_interop/chave_idx20_windows.json (0.09 MB)

[OK] Arquivo e chaves importados para o notebook:
  - Arquivo NOAA............: /home/alvaro/cip_viana/arquivos/noaa_gsod_2023.tar.gz
  - Chave Linux (IDX 18)....: /home/alvaro/cip_viana/chaves_interop/chave_idx18_linux.json
  - Chave Windows (IDX 20)..: /home/alvaro/cip_viana/chaves_interop/chave_idx20_windows.json

Tamanho do arquivo NOAA: 108.78 MB


## CÉLULA 5 — Carregar / exibir metadados essenciais das chaves

Esta célula mostra para o usuário que:

as chaves correspondem ao mesmo arquivo,

porém foram emitidas por SDKs diferentes,

com IDX distintos,

e que isso não é problema para a interoperabilidade.

In [5]:
# ============================================================
# CÉLULA — Inspeção das chaves IDX 18 (Linux) e IDX 20 (Windows)
# ============================================================

import json

def carregar_json(p):
    with open(p, "r", encoding="utf-8") as f:
        return json.load(f)

def extrair_hash_v3(chave):
    """
    Versão robusta: extrai o hash de integridade das chaves v3 híbridas.
    """
    campos = [
        "assinatura_integridade_final",
        "assinatura_integridade_chave_cipt",
    ]
    for c in campos:
        if c in chave and chave[c]:
            return chave[c]
    return None

def resumo_v3(chave, nome):
    print(f"[{nome}]")
    print(f"  - idx.............: {chave.get('sdk_idx_usado')}")
    print(f"  - N (dimensões)...: {chave.get('matrix_size_N_usado')}")
    print(f"  - arquivo..........: {chave.get('arquivo_original_nome')}")
    print(f"  - operação.........: {chave.get('operacao')}")
    print(f"  - data/hora........: {chave.get('timestamp_operacao_str')}")

    h = extrair_hash_v3(chave)
    if h:
        print(f"  - hash_integridade.: {h[:32]}...")
    else:
        print("  - hash_integridade.: [não encontrado]")

    # segurança: exibe presença da matriz P (não imprime)
    print(f"  - matriz_p........: {'OK' if chave.get('matriz_p_base64') else 'ausente'}")
    print()


# Carregar chaves locais baixadas
ch18 = carregar_json(CHAVE_LINUX_LOCAL)
ch20 = carregar_json(CHAVE_WINDOWS_LOCAL)

print("=== INSPEÇÃO DAS CHAVES — CIP-T v3 HÍBRIDO ===\n")

resumo_v3(ch18, "Chave Linux IDX 18")
resumo_v3(ch20, "Chave Windows IDX 20")

print(
    "Ambas as chaves foram produzidas sobre o MESMO arquivo NOAA.\n"
    "Elas diferem apenas pelo IDX e pela plataforma usada na assinatura.\n"
    "O binário CIP deste notebook deverá validar AMBAS — essa é a essência\n"
    "da interoperabilidade espectral da CIP.\n"
)


=== INSPEÇÃO DAS CHAVES — CIP-T v3 HÍBRIDO ===

[Chave Linux IDX 18]
  - idx.............: 18
  - N (dimensões)...: 1024
  - arquivo..........: noaa_gsod_2023.tar.gz
  - operação.........: assinatura_total_cipt_v3_hibrido
  - data/hora........: 20251124_115945
  - hash_integridade.: 77f210ad293d2957a514f2a1e44fe2be...
  - matriz_p........: OK

[Chave Windows IDX 20]
  - idx.............: 20
  - N (dimensões)...: 1024
  - arquivo..........: noaa_gsod_2023.tar.gz
  - operação.........: assinatura_total_cipt_v3_hibrido
  - data/hora........: 20251124_120307
  - hash_integridade.: b660f961b8dee7fabc0cad8d3456a8f9...
  - matriz_p........: OK

Ambas as chaves foram produzidas sobre o MESMO arquivo NOAA.
Elas diferem apenas pelo IDX e pela plataforma usada na assinatura.
O binário CIP deste notebook deverá validar AMBAS — essa é a essência
da interoperabilidade espectral da CIP.



## CÉLULA 6 — Verificação Cruzada de Interoperabilidade

Ou seja:

Usar o binário local do notebook (Linux ou Windows, tanto faz — o ponto é: “um binário único”)

Para verificar:

* o arquivo NOAA com a chave Linux IDX 18

* o arquivo NOAA com a chave Windows IDX 20

A interoperabilidade só é provada se:

* **Ambas as verificações retornarem sucesso (returncode == 0)**,

* Mesmo cada chave tendo sido produzida em **outro sistema operacional**

* E com **Outro IDX**

Isso demonstra que:

> A CIP não depende do SO, nem do compilador, nem da máquina.  
> O que importa é a coerência espectral do arquivo com o IDX.  
> Se isso for mantido, qualquer binário válido deve verificar qualquer chave válida.

In [6]:
# ============================================================
# CÉLULA — Verificação Cruzada de Interoperabilidade
# ============================================================

print("\n=== VERIFICAÇÃO CRUZADA — INTEROPERABILIDADE CIP ===\n")

def verificar_cipt(arquivo, chave_json, nome):
    """
    Executa o binário CIP local usando uma chave CIPT proveniente
    de outro ambiente (Linux ↔ Windows).
    """
    print(f"\n--- Verificando com {nome} ---")
    proc, t = run_cip(["-t", "verificar", str(arquivo), str(chave_json)])

    print("\n[STDOUT]\n", proc.stdout)

    if proc.returncode == 0:
        print(f"[OK] Verificação BEM-SUCEDIDA ({t:.3f} s) — interoperabilidade confirmada.")
    else:
        print("\n[STDERR]\n", proc.stderr)
        raise RuntimeError(
            f"FALHA: A verificação cruzada falhou usando {nome}. "
            "Isso não deveria ocorrer — investigar imediatamente."
        )

# Executar verificações cruzadas
verificar_cipt(ARQ_LOCAL, CHAVE_LINUX_LOCAL, "Chave Linux IDX 18 (assinada em outro SO)")
verificar_cipt(ARQ_LOCAL, CHAVE_WINDOWS_LOCAL, "Chave Windows IDX 20 (assinada em outro SO)")

print("\n=== RESULTADO ===")
print("Ambas as verificações foram realizadas com o MESMO binário CIP local.\n"
      "Isso demonstra, de forma pública e reprodutível, que o protocolo CIP opera\n"
      "com TOTAL independência de plataforma, compilador e sistema operacional.")



=== VERIFICAÇÃO CRUZADA — INTEROPERABILIDADE CIP ===


--- Verificando com Chave Linux IDX 18 (assinada em outro SO) ---

[STDOUT]
 [INFO] OpenMP: 18 threads.
[INFO] Eigen: 18 threads.
[INFO] CIP SDK em modo ilimitado: contador de créditos desativado.

════════════════[ CIP - Configuração SDK ]════════════════
[INFO] Idx do SDK determinado automaticamente: 18
[SUCESSO] Configuração do SDK (idx 18) carregada com sucesso.
[INFO] Idx da matriz de Assinatura (pré-calculada): 18 | Idx da matriz de Cifragem (pré-calculada): 19

════════════[ CIP - Verificação (MODO TOTAL) ]════════════
[INFO] Arquivo a ser verificado: noaa_gsod_2023.tar.gz
[INFO] Chave CIPT usada: chave_idx18_linux.json
[INFO] Verificando integridade da própria chave CIP-T...
[INFO] Hash esperado (assinatura_integridade_chave_cipt): 46a81b7ee6fafd983d764ab43e7d46f07f8a2806019adbd9a2a347e1566bd85b
[INFO] Hash calculado: 46a81b7ee6fafd983d764ab43e7d46f07f8a2806019adbd9a2a347e1566bd85b
[SUCESSO] Integridade da propria chave as

## CÉLULA 7 — Tabela comparativa das chaves (Linux IDX 18 vs Windows IDX 20)

In [7]:
# ============================================================
# CÉLULA 7 — Tabela comparativa das chaves (IDX 18 vs IDX 20)
# ============================================================

import pandas as pd

def linha_resumo(chave, origem):
    return {
        "origem": origem,
        "arquivo": chave.get("arquivo_original_nome"),
        "sdk_idx_usado": chave.get("sdk_idx_usado"),
        "N": chave.get("matrix_size_N_usado"),
        "operacao": chave.get("operacao"),
        "tamanho_bytes": chave.get("tamanho_original_bytes"),
        "timestamp": chave.get("timestamp_operacao_str"),
        "hash_chave": chave.get("assinatura_integridade_chave_cipt")[:16] + "...",
        "hash_arquivo": chave.get("assinatura_integridade_final")[:16] + "...",
    }

df_chaves = pd.DataFrame([
    linha_resumo(ch18, "Linux (SDK IDX 18)"),
    linha_resumo(ch20, "Windows (SDK IDX 20)")
])

display(df_chaves)

print(
    "\nAmbas as linhas se referem ao MESMO arquivo, com o MESMO tamanho e a MESMA dimensão N.\n"
    "Os hashes finais são distintos porque cada SDK utiliza uma base harmônica própria (idx\n"
    "diferente), mas ambos são revalidados com sucesso pelo mesmo binário CIP deste notebook."
)


origem                arquivo  sdk_idx_usado     N  \
0    Linux (SDK IDX 18)  noaa_gsod_2023.tar.gz             18  1024   
1  Windows (SDK IDX 20)  noaa_gsod_2023.tar.gz             20  1024   

                           operacao  tamanho_bytes        timestamp  \
0  assinatura_total_cipt_v3_hibrido      108776234  20251124_115945   
1  assinatura_total_cipt_v3_hibrido      108776234  20251124_120307   

            hash_chave         hash_arquivo  
0  46a81b7ee6fafd98...  77f210ad293d2957...  
1  550812b6bdd698b2...  b660f961b8dee7fa...


Ambas as linhas se referem ao MESMO arquivo, com o MESMO tamanho e a MESMA dimensão N.
Os hashes finais são distintos porque cada SDK utiliza uma base harmônica própria (idx
diferente), mas ambos são revalidados com sucesso pelo mesmo binário CIP deste notebook.


## CÉLULA 8 — Corrupção de 1 bit + Verificação Cruzada (Linux idx18 e Windows idx20)

In [8]:
# ============================================================
# CÉLULA — Corrupção de 1 bit + Verificação Cruzada
# ============================================================

import os
import random
import shutil
from pathlib import Path

print("\n=== TESTE CRUZADO — DETECÇÃO DE CORRUPÇÃO (1 BIT) ===")

# ------------------------------------------------------------
# 1. Criar uma cópia do arquivo e corromper 1 bit
# ------------------------------------------------------------
arquivo_corrompido = ARQ_LOCAL.parent / f"{ARQ_LOCAL.stem}_1bit{ARQ_LOCAL.suffix}"
shutil.copy2(ARQ_LOCAL, arquivo_corrompido)

def flip_bit(path: Path):
    with open(path, "r+b") as f:
        f.seek(0, os.SEEK_END)
        tamanho = f.tell()
        pos = random.randint(0, tamanho - 1)
        bit = random.randint(0, 7)

        f.seek(pos)
        original = f.read(1)[0]

        novo = original ^ (1 << bit)
        f.seek(pos)
        f.write(bytes([novo]))

    return pos, bit, original, novo

pos, bit, antigo, novo = flip_bit(arquivo_corrompido)

print(
    f"[INFO] 1 bit corrompido em posição byte {pos}, bit {bit} "
    f"({antigo:02x} → {novo:02x})"
)

# ------------------------------------------------------------
# 2. Verificar com chave Linux (idx 18)
# ------------------------------------------------------------
print("\n--- Verificando com chave Linux IDX 18 ---")

proc_lin, t_lin = run_cip([
    "-t", "verificar", str(arquivo_corrompido), str(CHAVE_LINUX_LOCAL)
])

print("\n[STDOUT]\n", proc_lin.stdout)

falha_linux = proc_lin.returncode != 0

if falha_linux:
    print(f"[OK] Chave Linux detectou a corrupção — tempo {t_lin:.3f} s")
else:
    print("[ERRO CRÍTICO] A chave Linux NÃO detectou a corrupção!")
    raise RuntimeError("Falha inesperada na verificação com chave Linux.")

# ------------------------------------------------------------
# 3. Verificar com chave Windows (idx 20)
# ------------------------------------------------------------
print("\n--- Verificando com chave Windows IDX 20 ---")

proc_win, t_win = run_cip([
    "-t", "verificar", str(arquivo_corrompido), str(CHAVE_WINDOWS_LOCAL)
])

print("\n[STDOUT]\n", proc_win.stdout)

falha_windows = proc_win.returncode != 0

if falha_windows:
    print(f"[OK] Chave Windows detectou a corrupção — tempo {t_win:.3f} s")
else:
    print("[ERRO CRÍTICO] A chave Windows NÃO detectou a corrupção!")
    raise RuntimeError("Falha inesperada na verificação com chave Windows.")

# ------------------------------------------------------------
# 4. Resultado Final
# ------------------------------------------------------------
print("\n=== RESULTADO FINAL ===")
if falha_linux and falha_windows:
    print(
        "As DUAS chaves (Linux idx18 e Windows idx20) rejeitaram o\n"
        "MESMO arquivo corrompido — interoperabilidade COMPLETA.\n"
        "A estrutura espectral não admite falsos positivos."
    )
else:
    print("Há inconsistência inesperada — investigar.")



=== TESTE CRUZADO — DETECÇÃO DE CORRUPÇÃO (1 BIT) ===
[INFO] 1 bit corrompido em posição byte 857000, bit 4 (c9 → d9)

--- Verificando com chave Linux IDX 18 ---

[STDOUT]
 [INFO] OpenMP: 18 threads.
[INFO] Eigen: 18 threads.
[INFO] CIP SDK em modo ilimitado: contador de créditos desativado.

════════════════[ CIP - Configuração SDK ]════════════════
[INFO] Idx do SDK determinado automaticamente: 18
[SUCESSO] Configuração do SDK (idx 18) carregada com sucesso.
[INFO] Idx da matriz de Assinatura (pré-calculada): 18 | Idx da matriz de Cifragem (pré-calculada): 19

════════════[ CIP - Verificação (MODO TOTAL) ]════════════
[INFO] Arquivo a ser verificado: noaa_gsod_2023.tar_1bit.gz
[INFO] Chave CIPT usada: chave_idx18_linux.json
[INFO] Verificando integridade da própria chave CIP-T...
[INFO] Hash esperado (assinatura_integridade_chave_cipt): 46a81b7ee6fafd983d764ab43e7d46f07f8a2806019adbd9a2a347e1566bd85b
[INFO] Hash calculado: 46a81b7ee6fafd983d764ab43e7d46f07f8a2806019adbd9a2a347e1566b

## CÉLULA 9 — Encerramento específico da interoperabilidade (Markdown)

# Encerramento — Interoperabilidade Espectral da CIP

Este notebook documenta, de forma pública e reprodutível, que a Cifra de Integridade Primal (CIP):  

1. **Assina o mesmo arquivo público em ambientes distintos**  
   - Uma chave foi gerada em Linux (SDK IDX 18).  
   - Outra chave foi gerada em Windows (SDK IDX 20).  
   - Ambas em modo TOTAL, sobre o mesmo arquivo NOAA (`noaa_gsod_2023.tar.gz`), com `N = 1024`.

2. **Verifica ambas as chaves com um único binário nativo**  
   O binário CIP local (deste notebook), executando em um único sistema operacional, validou:  
   - a chave Linux (idx 18) usando sua base harmônica local;  
   - a chave Windows (idx 20) usando a matriz embutida na própria chave.

3. **Diferencia claramente o papel do IDX**  
   O `sdk_idx_usado` identifica a base harmônica associada à assinatura:  
   - se o idx da chave coincide com o idx local, a verificação usa a matriz pré-calculada do SDK;  
   - se o idx da chave for externo, a verificação utiliza a matriz embutida na chave CIP-T.

   Em ambos os casos, o critério de aceitação é o mesmo:   
   o hash de integridade final do arquivo precisa coincidir exatamente com o registrado na chave.

4. **Mostra que não há dependência de plataforma, compilador ou ambiente**  
   A integridade não depende do sistema operacional, do compilador ou da máquina utilizada para gerar  
   a assinatura. O que importa é a coerência espectral entre:  
   - o conteúdo do arquivo,
   - a base harmônica (idx) utilizada,
   - e a estrutura matricial registrada na chave.

5. **Reforça o caráter universal da estrutura**  
   O fato de um único binário validar chaves produzidas em ambientes distintos, com idx distintos, sem  
   qualquer ajuste manual, reforça que a CIP opera sobre uma estrutura aritmética estável e universal.  
   Não há margem para “compatibilização” ad hoc: ou o espectro bate, ou a verificação falha.

---

Do ponto de vista institucional, este experimento mostra que:

- é possível definir um **protocolo único de integridade** baseado em uma régua espectral comum;  
- diferentes implementações (SDKs, idx, plataformas) podem coexistir sem perda de verificabilidade;  
- qualquer instituição pode verificar, de forma independente, assinaturas produzidas em outro ambiente,  
  desde que respeitada a mesma base estrutural.

A interoperabilidade aqui demonstrada não é um detalhe técnico:  
é a evidência de que a CIP se comporta como um **protocolo de integridade universal**, e não como uma  
biblioteca isolada dependente de ambiente.
